<h2><center>Random Submission for Clouds Removal</center></h2>

![](https://media.discordapp.net/attachments/703945836614123561/866939997021143040/banner.jpg?width=1439&height=277)

**Note : Create a copy of the notebook and use the copy for submission. Go to *File > Save a Copy in Drive* to create a new copy**

# Setting up Environment

### Downloading Dataset

So we will first need to download the python library by AIcrowd that will allow us to download the dataset by just inputting the API key. 

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!cp drive/MyDrive/complete_final_data_with_val.zip ./
!unzip complete_final_data_with_val.zip

Streaming output truncated to the last 5000 lines.
  inflating: testA/test/160_9.jpg    
  inflating: testA/test/477_10.jpg   
  inflating: testA/test/100_10.jpg   
  inflating: testA/test/485_9.jpg    
  inflating: testA/test/232_8.jpg    
  inflating: testA/test/381_18.jpg   
  inflating: testA/test/401_2.jpg    
  inflating: testA/test/33_18.jpg    
  inflating: testA/test/484_19.jpg   
  inflating: testA/test/6_9.jpg      
  inflating: testA/test/355_7.jpg    
  inflating: testA/test/272_9.jpg    
  inflating: testA/test/447_12.jpg   
  inflating: testA/test/343_8.jpg    
  inflating: testA/test/256_20.jpg   
  inflating: testA/test/417_1.jpg    
  inflating: testA/test/43_15.jpg    
  inflating: testA/test/52_0.jpg     
  inflating: testA/test/103_14.jpg   
  inflating: testA/test/35_23.jpg    
  inflating: testA/test/440_23.jpg   
  inflating: testA/test/155_0.jpg    
  inflating: testA/test/409_2.jpg    
  inflating: testA/test/102_2.jpg    
  inflating: testA/test/53_23.jpg    

In [39]:
!rm -rf checkpoints
!rm 512_checkpoints.zip
!cp drive/MyDrive/512_checkpoints.zip ./
!unzip 512_checkpoints.zip

Archive:  512_checkpoints.zip
   creating: checkpoints/
   creating: checkpoints/clouds/
  inflating: checkpoints/clouds/14_net_D.pth  
  inflating: checkpoints/clouds/10_net_G.pth  
  inflating: checkpoints/clouds/2_net_G.pth  
  inflating: checkpoints/clouds/latest_net_G.pth  
  inflating: checkpoints/clouds/6_net_D.pth  
  inflating: checkpoints/clouds/8_net_G.pth  
  inflating: checkpoints/clouds/2_net_D.pth  
  inflating: checkpoints/clouds/14_net_G.pth  
  inflating: checkpoints/clouds/4_net_G.pth  
  inflating: checkpoints/clouds/8_net_D.pth  
  inflating: checkpoints/clouds/loss_log.txt  
  inflating: checkpoints/clouds/latest_net_D.pth  
   creating: checkpoints/clouds/web/
   creating: checkpoints/clouds/web/images/
  inflating: checkpoints/clouds/web/images/epoch008_fake_B.png  
  inflating: checkpoints/clouds/web/images/epoch007_fake_B.png  
  inflating: checkpoints/clouds/web/images/epoch005_fake_B.png  
  inflating: checkpoints/clouds/web/images/epoch010_real_A.png  
  in

In [4]:
!pip install aicrowd-cli

%load_ext aicrowd.magic

     |████████████████████████████████| 43 kB 1.5 MB/s 
     |████████████████████████████████| 209 kB 5.1 MB/s 
     |████████████████████████████████| 170 kB 37.6 MB/s 
     |████████████████████████████████| 62 kB 765 kB/s 
     |████████████████████████████████| 54 kB 2.4 MB/s 
     |████████████████████████████████| 76 kB 4.1 MB/s 
     |████████████████████████████████| 63 kB 1.8 MB/s 
     |████████████████████████████████| 51 kB 6.7 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0
  Attempting uninstall: tqdm
    Found existing installation: tqdm 4.41.1
    Uninstalling tqdm-4.41.1:
      Successfully uninstalled tqdm-4.41.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires requests~=2.23.0, but you have reque

In [5]:
%aicrowd login --api-key c18a6c4b759fa2df29481af274df6942

API Key valid
Saved API Key successfully!


In [ ]:
# # Downloading the Dataset
# !rm -rf data
# !mkdir data
# !aicrowd dataset download -c clouds-removal "*Partial*" -o data
# !aicrowd dataset download -c clouds-removal "*Complete*" -o data

test.zip: 100% 601M/601M [00:40<00:00, 14.9MB/s]
train.zip: 100% 1.62G/1.62G [02:34<00:00, 10.5MB/s]


In [ ]:
# # # Unzipping the dataset
# !unzip data/train.zip -d data/train >> /dev/null
# !unzip data/test.zip -d data/test >> /dev/null

# Importing Libraries

In [6]:
# Importing Libraries
import os
import numpy as np
import random
import torch
from natsort import natsorted
from glob import glob
import cv2
from tqdm.notebook import tqdm

In [ ]:
# all_files = os.listdir('data/train')
# num_total = int(len(all_files) / 2)

In [7]:
def seed_everything(seed):
  os.environ["PL_GLOBAL_SEED"] = str(seed)
  random.seed(seed)
  np.random.seed(seed)
  torch.manual_seed(seed)
  torch.cuda.manual_seed_all(seed)

seed_everything(1)

In [ ]:
# indexes = [i for i in range(num_total)]
# val_idxes = random.sample(indexes, 5)
# val_idxes[0]

# val_idxes = []

In [ ]:
# !rm -rf my_data
# !rm -rf testA
# !mkdir my_data
# !mkdir my_data/A
# !mkdir my_data/B
# !mkdir my_data/A/train
# !mkdir my_data/A/val
# !mkdir my_data/B/train
# !mkdir my_data/B/val
# !mkdir testA
# !mkdir testA/test

# for cloud_video in natsorted(glob('data/train/cloud*')):
#   current = int(cloud_video.split('.')[0].split('_')[1])
#   img_video = cv2.VideoCapture(cloud_video)
#   # Going through each frame
#   index = 0
#   while True:
#     # Reading the frame
#     ret, frame = img_video.read()
#     if ret:
#       if current in val_idxes:
#         cv2.imwrite(f'my_data/A/val/{current}_{index}.jpg', frame)
#       else:
#         cv2.imwrite(f'my_data/A/train/{current}_{index}.jpg', frame)
#       index += 1
#     else:
#       break

# for clear_video in natsorted(glob('data/train/clear*')):
#   current = int(clear_video.split('.')[0].split('_')[1])
#   img_video = cv2.VideoCapture(clear_video)
#   # Going through each frame
#   index = 0
#   while True:
#     # Reading the frame
#     ret, frame = img_video.read()
#     if ret:
#       if current in val_idxes:
#         cv2.imwrite(f'my_data/B/val/{current}_{index}.jpg', frame)
#       else:
#         cv2.imwrite(f'my_data/B/train/{current}_{index}.jpg', frame)
#       index += 1
#     else:
#       break

# for cloud_video in natsorted(glob('data/test/*')):
#   current = int(cloud_video.split('.')[0].split('_')[1])
#   img_video = cv2.VideoCapture(cloud_video)
#   # Going through each frame
#   index = 0
#   while True:
#     # Reading the frame
#     ret, frame = img_video.read()
#     if ret:
#       cv2.imwrite(f'testA/test/{current}_{index}.jpg', frame)
#       index += 1
#     else:
#       break

In [ ]:
# !zip -r partial_cloud.zip my_data

In [ ]:
# !cp partial_cloud.zip drive/MyDrive

In [8]:
!git clone https://github.com/junyanz/pytorch-CycleGAN-and-pix2pix.git

Cloning into 'pytorch-CycleGAN-and-pix2pix'...
remote: Enumerating objects: 2340, done.
remote: Total 2340 (delta 0), reused 0 (delta 0), pack-reused 2340
Receiving objects: 100% (2340/2340), 8.09 MiB | 7.41 MiB/s, done.
Resolving deltas: 100% (1501/1501), done.


In [ ]:
# !rm -rf final_data
# !cd pytorch-CycleGAN-and-pix2pix && python3 datasets/combine_A_and_B.py --fold_A ../my_data/A --fold_B ../my_data/B --fold_AB ../final_data

# Training

In [9]:
!pip install dominate
!pip install visdom

     |████████████████████████████████| 676 kB 4.2 MB/s 
     |████████████████████████████████| 68 kB 4.3 MB/s 
  Created wheel for visdom: filename=visdom-0.1.8.9-py3-none-any.whl size=655249 sha256=baab6df7ee5153cc6cd84eec2f6ee37074578fa0ae060487ebcbf5f78d619853
  Stored in directory: /root/.cache/pip/wheels/2d/d1/9b/cde923274eac9cbb6ff0d8c7c72fe30a3da9095a38fd50bbf1
  Created wheel for torchfile: filename=torchfile-0.1.0-py3-none-any.whl size=5710 sha256=064056306400f29e5386231b62884dee916854bd2462315841b6d193187a1e84
  Stored in directory: /root/.cache/pip/wheels/ac/5c/3a/a80e1c65880945c71fd833408cd1e9a8cb7e2f8f37620bb75b
Successfully built visdom torchfile


In [9]:
!rm -rf checkpoints
!cd pytorch-CycleGAN-and-pix2pix && python3 train.py --dataroot ../final_data --name clouds --model pix2pix --direction AtoB --checkpoints_dir ../checkpoints --batch_size 4 --n_epochs 10 --n_epochs_decay 0 --gan_mode lsgan --save_epoch_freq 1 --preprocess none --display_id -1 --load_size 512 --crop_size 512

Streaming output truncated to the last 5000 lines.
(epoch: 5, iters: 40176, time: 0.073, data: 0.006) G_GAN: 0.367 G_L1: 7.747 D_real: 0.265 D_fake: 0.048 
(epoch: 5, iters: 40276, time: 0.073, data: 0.010) G_GAN: 0.434 G_L1: 7.433 D_real: 0.442 D_fake: 0.093 
(epoch: 5, iters: 40376, time: 0.073, data: 0.009) G_GAN: 0.624 G_L1: 9.106 D_real: 0.145 D_fake: 0.214 
(epoch: 5, iters: 40476, time: 0.073, data: 0.007) G_GAN: 0.330 G_L1: 7.937 D_real: 0.181 D_fake: 0.212 
(epoch: 5, iters: 40576, time: 0.147, data: 0.006) G_GAN: 0.445 G_L1: 8.160 D_real: 0.118 D_fake: 0.131 
(epoch: 5, iters: 40676, time: 0.075, data: 0.013) G_GAN: 0.444 G_L1: 7.949 D_real: 0.112 D_fake: 0.274 
(epoch: 5, iters: 40776, time: 0.073, data: 0.007) G_GAN: 0.644 G_L1: 8.137 D_real: 0.073 D_fake: 0.574 
(epoch: 5, iters: 40876, time: 0.073, data: 0.008) G_GAN: 0.373 G_L1: 7.082 D_real: 0.260 D_fake: 0.078 
(epoch: 5, iters: 40976, time: 0.073, data: 0.006) G_GAN: 0.578 G_L1: 8.584 D_real: 0.109 D_fake: 0.219 
(epo

In [ ]:
# # !rm -rf checkpoints
# !cd pytorch-CycleGAN-and-pix2pix && python3 train.py --dataroot ../final_data --name clouds --model pix2pix --direction AtoB --checkpoints_dir ../checkpoints --batch_size 4 --n_epochs 10 --n_epochs_decay 10 --gan_mode lsgan --save_epoch_freq 2 --display_id -1

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:281: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:281: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:281: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  "Argument interpolation should be of type InterpolationMode instead of int. "
/usr/local/lib/python3.7/dist-packages/torchvision/transforms/transforms.py:281: UserWarning: 

In [10]:
!zip -r web.zip checkpoints/clouds/web

  adding: checkpoints/clouds/web/ (stored 0%)
  adding: checkpoints/clouds/web/images/ (stored 0%)
  adding: checkpoints/clouds/web/images/epoch008_fake_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch007_fake_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch005_fake_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch010_real_A.png (deflated 1%)
  adding: checkpoints/clouds/web/images/epoch010_real_B.png (deflated 1%)
  adding: checkpoints/clouds/web/images/epoch012_real_A.png (deflated 1%)
  adding: checkpoints/clouds/web/images/epoch001_real_B.png (deflated 1%)
  adding: checkpoints/clouds/web/images/epoch005_real_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch001_fake_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch013_fake_B.png (deflated 0%)
  adding: checkpoints/clouds/web/images/epoch005_real_A.png (deflated 1%)
  adding: checkpoints/clouds/web/images/epoch014_real_A.png (deflated 0%)
  adding: che

In [23]:
!cd pytorch-CycleGAN-and-pix2pix && python3 test.py --dataroot ../final_data --name clouds --model pix2pix --direction AtoB --checkpoints_dir ../checkpoints --preprocess none --load_size 512 --crop_size 512 --phase val --results_dir ../results

----------------- Options ---------------
             aspect_ratio: 1.0                           
               batch_size: 1                             
          checkpoints_dir: ../checkpoints                	[default: ./checkpoints]
                crop_size: 512                           	[default: 256]
                 dataroot: ../final_data                 	[default: None]
             dataset_mode: aligned                       
                direction: AtoB                          
          display_winsize: 256                           
                    epoch: latest                        
                     eval: False                         
                  gpu_ids: 0                             
                init_gain: 0.02                          
                init_type: normal                        
                 input_nc: 3                             
                  isTrain: False                         	[default: None]
                

# Generate Submission

In this section we will be generating a random submission. We will read all of the files from the tesing directroy and save the same video in `clear` directory for submsision. 

In [ ]:
!zip -r 512_checkpoints.zip checkpoints
!cp 512_checkpoints.zip drive/MyDrive

In [68]:
!rm -rf new_testA
!mkdir new_testA
!mkdir new_testA/test
for img in os.listdir('testA/test'):
  new_img = Image.new('RGB', (1024, 512))
  orig_img = Image.open(f'testA/test/{img}')
  new_img.paste(orig_img)
  new_img.save(f'new_testA/test/{img}')
print(len(os.listdir('new_testA/test')))

12000


In [69]:
!rm -rf results
!cd pytorch-CycleGAN-and-pix2pix && python3 test.py --dataroot ../new_testA --name clouds --model test --direction AtoB --dataset_mode single --checkpoints_dir ../checkpoints --netG unet_256 --norm batch --dataset_mode aligned --results_dir ../results --num_test 12000 --load_size 512 --crop_size 512

----------------- Options ---------------
             aspect_ratio: 1.0                           
               batch_size: 1                             
          checkpoints_dir: ../checkpoints                	[default: ./checkpoints]
                crop_size: 512                           	[default: 256]
                 dataroot: ../new_testA                  	[default: None]
             dataset_mode: aligned                       	[default: single]
                direction: AtoB                          
          display_winsize: 256                           
                    epoch: latest                        
                     eval: False                         
                  gpu_ids: 0                             
                init_gain: 0.02                          
                init_type: normal                        
                 input_nc: 3                             
                  isTrain: False                         	[default: None

In [ ]:
# !rm -rf results
# !cd pytorch-CycleGAN-and-pix2pix && python3 test.py --dataroot ../testA --name clouds --model test --direction AtoB --dataset_mode single --checkpoints_dir ../checkpoints --netG unet_256 --norm batch --dataset_mode aligned --results_dir ../results --num_test 12000 --epoch latest

In [70]:
from tqdm import tqdm

# Generating Predictions Function
def gen_predictions():
  !rm -rf clear
  !mkdir clear
  for index in tqdm(range(500)):
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = cv2.VideoWriter(os.path.join("clear", f"clear_{index}.mp4"), fourcc, 24.0, (512,512))
    video_images = [f'results/clouds/test_latest/images/{index}_{i}_fake.png' for i in range(24)]
    for image in video_images:
      assert os.path.isfile(image)
      frame = cv2.imread(image)
      frame = cv2.resize(frame, (512, 512))
      out.write(frame)

In [71]:
!zip -r 512_results.zip results
!cp 512_results.zip drive/MyDrive

Streaming output truncated to the last 5000 lines.
  adding: results/clouds/test_latest/images/23_17_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/270_8_real.png (deflated 0%)
  adding: results/clouds/test_latest/images/414_1_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/120_8_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/34_12_real.png (deflated 0%)
  adding: results/clouds/test_latest/images/136_1_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/114_21_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/355_8_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/200_1_real.png (deflated 0%)
  adding: results/clouds/test_latest/images/310_16_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/395_1_fake.png (deflated 0%)
  adding: results/clouds/test_latest/images/63_0_real.png (deflated 0%)
  adding: results/clouds/test_latest/images/337_15_fake.png (deflated 0%

In [72]:
!zip -r new_testA.zip new_testA
!cp new_testA.zip drive/MyDrive

Streaming output truncated to the last 5000 lines.
  adding: new_testA/test/116_6.jpg (deflated 9%)
  adding: new_testA/test/341_3.jpg (deflated 14%)
  adding: new_testA/test/131_11.jpg (deflated 8%)
  adding: new_testA/test/43_7.jpg (deflated 8%)
  adding: new_testA/test/148_20.jpg (deflated 7%)
  adding: new_testA/test/331_18.jpg (deflated 6%)
  adding: new_testA/test/281_4.jpg (deflated 10%)
  adding: new_testA/test/394_2.jpg (deflated 13%)
  adding: new_testA/test/412_16.jpg (deflated 6%)
  adding: new_testA/test/489_0.jpg (deflated 11%)
  adding: new_testA/test/204_8.jpg (deflated 7%)
  adding: new_testA/test/442_19.jpg (deflated 7%)
  adding: new_testA/test/201_7.jpg (deflated 8%)
  adding: new_testA/test/382_17.jpg (deflated 7%)
  adding: new_testA/test/113_20.jpg (deflated 8%)
  adding: new_testA/test/439_11.jpg (deflated 6%)
  adding: new_testA/test/165_23.jpg (deflated 7%)
  adding: new_testA/test/345_1.jpg (deflated 12%)
  adding: new_testA/test/235_15.jpg (deflated 6%)
  ad

In [ ]:
gen_predictions()

 90%|████████▉ | 449/500 [03:57<00:26,  1.90it/s]

# Submitting Results 📄

## Uploading the Results

Using notebook: /content/drive/MyDrive/Colab Notebooks/Cloud Removal pix2pix for submission...
Scrubbing API keys from the notebook...
submission.zip ━━━━━━━━━━━━━━━━━━━━ 100.0% • 846.3/846.3 MB • 2.8 MB/s • 0:00:00
                                                ╭─────────────────────────╮                                                 
                                                │ Successfully submitted! │                                                 
                                                ╰─────────────────────────╯                                                 
                                                      Important links                                                       
┌──────────────────┬───────────────────────────────────────────────────────────────────────────────────────────────────────┐
│  This submission │ https://www.aicrowd.com/challenges/ai-blitz-x/problems/clouds-removal/submissions/152401              │
│                  │              

> Don't be shy to ask question related to any errors you are getting or doubts in any part of this notebook in [discussion forum](https://www.aicrowd.com/challenges/ai-blitz-10/problems/clouds-removal/discussion) or in [AIcrowd Discord sever](https://discord.gg/T6uZSWBMSZ), AIcrew will be happy to help you :)

Also, wanna give us your valuable feedback for next blitz or wanna work with us creating blitz challanges ? Let us know! 